In [1]:
import requests
import json
import pandas as pd
from bs4 import BeautifulSoup
import os
import re

In [2]:
client_id = "zuo60iNcVNsA5BmyfHL64nzVMAfZ-suiFONibf8_EjOPXeUQgrIqX-w3CA-RRji8"
client_secret = "KsD2On2pG2zR7vgvTLkp7zW5i3LHoKuIB8OqyN0uV-AAIocMwwi8JQTeaolFozKSvQpiQkH6V0wGh6Jr7qSW1w"
token = "_Q2Mi2ftYFYIkFAUPY9lfkROyNXdj5ML8_6riblV-YCcfHvEvhy5k5Ax5zcWvd-E"
artist_name = 'taylor swift'

### Functions to get urls to pages with song lyrics

In [3]:
def get_artist_info(artist_name, page):
    base_url = 'https://api.genius.com'
    headers = {'Authorization': 'Bearer ' + token}
    search_url = base_url + '/search?per_page=10&page=' + str(page)
    data = {'q': artist_name}
    response = requests.get(search_url, data=data, headers=headers)
    return response

def get_song_url(artist_name, song_cap):
    page = 1
    songs = []
    
    while True:
        response = get_artist_info(artist_name, page)
        json = response.json()
        
        song_info = []
        for hit in json['response']['hits']:
            if artist_name.lower() in hit['result']['primary_artist']['name'].lower():
                song_info.append(hit)
        
        for song in song_info:
            if (len(songs) < song_cap):
                url = song['result']['url']
                songs.append(url)
                
        if (len(songs) == song_cap):
            break
        else:
            page += 1
    
    print('Found {} songs by {}'.format(len(songs), artist_name))
    return songs

### Test the functions to get urls

In [ ]:
get_song_url(artist_name, 300)

### Function to get lyrics

In [4]:
def get_lyrics(url):
    page = requests.get(url)
    html = BeautifulSoup(page.text, 'html.parser')
    
    title = html.find('title')
    title_text = title.get_text()
    title_text = title_text.encode('ascii', errors='ignore').decode()
    song_title = title_text.replace("TaylorSwift  ", "").replace(" Lyrics | Genius Lyrics", " ")
    
    album = html.find('a', class_="PrimaryAlbum__Title-cuci8p-4 NcWGs")
    try:
        album_text = album.get_text()
    except AttributeError:
        album_title = 'unknown'
    else:
        album_title = album_text.encode('ascii', errors='ignore').decode()
        album_title = re.sub('(20((0[1-9])|([1-9][0-9])))', '', album_title)
        album_title = re.sub('[()]', '', album_title).strip()
        
    
    lyrics = html.find_all('div', class_="Lyrics__Container-sc-1ynbvzw-8 eOLwDW")
    full_lyrics = ''
    for section in lyrics:
        current_section = section.get_text()
        current_section = current_section.encode('ascii', errors='ignore').decode()
        full_lyrics = full_lyrics + current_section
    full_lyrics = re.sub(r'[\(\[].*?[\)\]]', '', full_lyrics)
    full_lyrics = os.linesep.join([s for s in full_lyrics.splitlines() if s])
    
    lyric_words = [word for word in full_lyrics.split(" ") if word != ""]
    obj = {}
    obj['song_title'] = song_title.lower()
    obj['album'] = album_title.lower()
    obj['lyrics'] = lyric_words
    return obj
    
#     title_and_lyrics[song_title.lower()] = full_lyrics
#     return title_and_lyrics    

### Test the function to get lyrics

In [5]:
lyrics = get_lyrics('https://genius.com/Taylor-swift-i-know-places-lyrics')
print(lyrics)

{'song_title': 'i know places ', 'album': '1989 deluxe', 'lyrics': ['I,', 'I,', 'I,', 'I,', 'I,', 'I,', 'I,', 'I-II,', 'I,', 'I,', 'I,', 'I,', 'I,', 'I,', 'I-II,', 'I,', 'I,', 'I,', 'I,', 'I,', 'I,', 'I-I', 'You', 'stand', 'with', 'your', 'hand', 'on', 'my', "waistlineIt's", 'a', 'scene', 'and', "we're", 'out', 'here', 'in', 'plain', 'sightI', 'can', 'hear', 'them', 'whisper', 'as', 'we', 'pass', "byIt's", 'a', 'bad', 'sign,', 'bad', 'signSomething', 'happens', 'when', 'everybody', 'finds', 'outSee', 'the', 'vultures', 'circling,', 'dark', "cloudsLove's", 'a', 'fragile', 'little', 'flame,', 'it', 'could', 'burn', 'outIt', 'could', 'burn', "out'Cause", 'they', 'got', 'the', 'cages,', 'they', 'got', 'the', 'boxes', 'and', 'gunsThey', 'are', 'the', 'hunters,', 'we', 'are', 'the', 'foxes', 'and', 'we', 'runBaby,', 'I', 'know', 'places', 'we', "won't", 'be', 'foundAnd', "they'll", 'be', 'chasing', 'their', 'tails', 'trying', 'to', 'track', 'us', "down'Cause", 'I,', 'I', 'know', 'places', 'w

### Group song lyrics by album

In [6]:
albums = ["taylor swift", "fearless", "speak now", "red deluxe edition", "1989 deluxe", "reputation", "lover", "folklore", "evermore"]
album_song_dict = {}
for album in albums:
    album_song_dict[album] = []

In [7]:
album_song_dict

{'taylor swift': [],
 'fearless': [],
 'speak now': [],
 'red deluxe edition': [],
 '1989 deluxe': [],
 'reputation': [],
 'lover': [],
 'folklore': [],
 'evermore': []}

### Define and run function to get urls + lyrics, and write output to json files

In [8]:
def write_lyrics_to_file(artist_name, song_count):
    all_songs = []
    urls = get_song_url(artist_name, song_count)
    for url in urls:
        title_and_lyrics = get_lyrics(url)
        all_songs.append(title_and_lyrics)
        
        if title_and_lyrics['album'] in album_song_dict.keys():
            album_song_dict[title_and_lyrics['album']].append(title_and_lyrics['lyrics'])
    
    with open('lyrics_taylor_swift.json', 'w') as f:
        json.dump(all_songs, f, indent=4)
    
    with open("album_lyrics_1.json", 'w') as f:
        json.dump(album_song_dict, f, indent=4)
    
write_lyrics_to_file(artist_name, 300)

Found 300 songs by taylor swift


### Open json file with lyrics

In [9]:
with open('lyrics_taylor_swift.json', 'r') as f:
    song_lyrics_obj = json.load(f)
song_lyrics_obj

[{'song_title': 'cardigan ',
  'album': 'folklore',
  'lyrics': ['Vintage',
   'tee,',
   'brand',
   'new',
   'phoneHigh',
   'heels',
   'on',
   'cobblestonesWhen',
   'you',
   'are',
   'young,',
   'they',
   'assume',
   'you',
   'knownothingSequinsmile,',
   'black',
   'lipstickSensualpoliticsWhen',
   'you',
   'are',
   'young,',
   'they',
   'assumeyou',
   'know',
   'nothingBut',
   'I',
   'knew',
   "youDancin'",
   'in',
   'your',
   "Levi'sDrunk",
   'under',
   'a',
   'streetlight,',
   'II',
   'knew',
   'youHand',
   'under',
   'my',
   'sweatshirtBaby,',
   'kiss',
   'it',
   'better,',
   'IAnd',
   'when',
   'I',
   'felt',
   'like',
   'I',
   'was',
   'an',
   'old',
   'cardiganUnder',
   "someone's",
   'bedYou',
   'put',
   'me',
   'on',
   'and',
   'said',
   'I',
   'was',
   'your',
   'favoriteA',
   'friend',
   'to',
   'all',
   'is',
   'a',
   'friend',
   'to',
   'noneChase',
   'two',
   'girls,',
   'lose',
   'the',
   'oneWhen',

### Open json file with lyrics grouped by album

In [10]:
with open('album_lyrics_1.json', 'r') as f:
    album_lyrics_obj = json.load(f)
album_lyrics_obj

{'taylor swift': [['Drew',
   'looks',
   'at',
   'meI',
   'fake',
   'a',
   'smile',
   'so',
   'he',
   "won't",
   'seeThat',
   'I',
   'want',
   'and',
   "I'm",
   'needingEverything',
   'that',
   'we',
   'should',
   "beI'll",
   'bet',
   "she's",
   'beautiful,',
   'that',
   'girl',
   'he',
   'talks',
   'aboutAnd',
   "she's",
   'got',
   'everything',
   'that',
   'I',
   'have',
   'to',
   'live',
   'withoutDrew',
   'talks',
   'to',
   'meI',
   'laugh',
   "'cause",
   "it's",
   'so',
   'damn',
   'funnyThat',
   'I',
   "can't",
   'even',
   'seeAnyone',
   'when',
   "he's",
   'with',
   'meHe',
   'says',
   "he's",
   'so',
   'in',
   'love,',
   "he's",
   'finally',
   'got',
   'it',
   'rightI',
   'wonder',
   'if',
   'he',
   'knows',
   "he's",
   'all',
   'I',
   'think',
   'about',
   'at',
   "nightHe's",
   'the',
   'reason',
   'for',
   'the',
   'teardrops',
   'on',
   'my',
   'guitarThe',
   'only',
   'thing',
   'that',
   

In [11]:
# go thru song_lyrics_obj for each of the song titles on my list, adding to the correct album in album_lyrics_obj
for song in song_lyrics_obj:
    if song['song_title'] == 'you need to calm down ':
        album_lyrics_obj['lover'].append(song['lyrics'])
    if song['song_title'] == 'lover ':
        album_lyrics_obj['lover'].append(song['lyrics'])
    if song['song_title'] == 'blank space ':
        album_lyrics_obj['1989 deluxe'].append(song['lyrics'])
    if song['song_title'] == '...ready for it? ':
        album_lyrics_obj['reputation'].append(song['lyrics'])
    if song['song_title'] == 'willow ':
        album_lyrics_obj['evermore'].append(song['lyrics'])
    if song['song_title'] == 'cruel summer ':
        album_lyrics_obj['lover'].append(song['lyrics'])
    if song['song_title'] == 'the archer ':
        album_lyrics_obj['lover'].append(song['lyrics'])
    if song['song_title'] == 'untouchable ':
        album_lyrics_obj['fearless'].append(song['lyrics'])
    if song['song_title'] == 'the man ':
        album_lyrics_obj['lover'].append(song['lyrics'])
    if song['song_title'] == 'bad blood ':
        album_lyrics_obj['reputation'].append(song['lyrics'])
    if song['song_title'] == 'miss americana & the heartbreak prince ':
        album_lyrics_obj['lover'].append(song['lyrics'])
    if song['song_title'] == 'london boy ':
        album_lyrics_obj['lover'].append(song['lyrics'])
    if song['song_title'] == 'cornelia street ':
        album_lyrics_obj['lover'].append(song['lyrics'])
    if song['song_title'] == 'wildest dreams ':
        album_lyrics_obj['1989 deluxe'].append(song['lyrics'])
    if song['song_title'] == 'daylight ':
        album_lyrics_obj['lover'].append(song['lyrics'])
    if song['song_title'] == 'death by a thousand cuts ':
        album_lyrics_obj['lover'].append(song['lyrics'])
    if song['song_title'] == 'i forgot that you existed ':
        album_lyrics_obj['lover'].append(song['lyrics'])
    if song['song_title'] == 'paper rings ':
        album_lyrics_obj['lover'].append(song['lyrics'])
    if song['song_title'] == 'false god ':
        album_lyrics_obj['lover'].append(song['lyrics'])
    if song['song_title'] == 'i think he knows ':
        album_lyrics_obj['lover'].append(song['lyrics'])
    if song['song_title'] == 'afterglow ':
        album_lyrics_obj['lover'].append(song['lyrics'])
    if song['song_title'] == "soon you'll get better ":
        album_lyrics_obj['lover'].append(song['lyrics'])
    if song['song_title'] == 'shake it off ':
        album_lyrics_obj['1989 deluxe'].append(song['lyrics'])
    if song['song_title'] == 'its nice to have a friend ':
        album_lyrics_obj['lover'].append(song['lyrics'])
    if song['song_title'] == 'everything has changed ':
        album_lyrics_obj['red deluxe edition'].append(song['lyrics'])
    if song['song_title'] == 'mean ':
        album_lyrics_obj['speak now'].append(song['lyrics'])
    if song['song_title'] == 'fifteen ':
        album_lyrics_obj['fearless'].append(song['lyrics'])
    if song['song_title'] == 'sparks fly ':
        album_lyrics_obj['speak now'].append(song['lyrics'])
    if song['song_title'] == 'picture to burn ':
        album_lyrics_obj['taylor swift'].append(song['lyrics'])
    if song['song_title'] == 'the story of us ':
        album_lyrics_obj['speak now'].append(song['lyrics'])
    if song['song_title'] == 'ours ':
        album_lyrics_obj['speak now'].append(song['lyrics'])
    if song['song_title'] == 'tim mcgraw ':
        album_lyrics_obj['taylor swift'].append(song['lyrics'])
    if song['song_title'] == 'cold as you ':
        album_lyrics_obj['taylor swift'].append(song['lyrics'])
    if song['song_title'] == 'tied together with a smile ':
        album_lyrics_obj['taylor swift'].append(song['lyrics'])
    if song['song_title'] == 'the other side of the door ':
        album_lyrics_obj['fearless'].append(song['lyrics'])
    if song['song_title'] == 'jump then fall ':
        album_lyrics_obj['fearless'].append(song['lyrics'])
    if song['song_title'] == 'if this was a movie ':
        album_lyrics_obj['speak now'].append(song['lyrics'])
    if song['song_title'] == 'im only me when im with you ':
        album_lyrics_obj['taylor swift'].append(song['lyrics'])
    if song['song_title'] == 'superstar ':
        album_lyrics_obj['fearless'].append(song['lyrics'])
    if song['song_title'] == 'come in with the rain ':
        album_lyrics_obj['fearless'].append(song['lyrics'])
    if song['song_title'] == 'superman ':
        album_lyrics_obj['speak now'].append(song['lyrics'])
    if song['song_title'] == 'today was a fairytale ':
        album_lyrics_obj['fearless'].append(song['lyrics'])

In [12]:
album_lyrics_obj

{'taylor swift': [['Drew',
   'looks',
   'at',
   'meI',
   'fake',
   'a',
   'smile',
   'so',
   'he',
   "won't",
   'seeThat',
   'I',
   'want',
   'and',
   "I'm",
   'needingEverything',
   'that',
   'we',
   'should',
   "beI'll",
   'bet',
   "she's",
   'beautiful,',
   'that',
   'girl',
   'he',
   'talks',
   'aboutAnd',
   "she's",
   'got',
   'everything',
   'that',
   'I',
   'have',
   'to',
   'live',
   'withoutDrew',
   'talks',
   'to',
   'meI',
   'laugh',
   "'cause",
   "it's",
   'so',
   'damn',
   'funnyThat',
   'I',
   "can't",
   'even',
   'seeAnyone',
   'when',
   "he's",
   'with',
   'meHe',
   'says',
   "he's",
   'so',
   'in',
   'love,',
   "he's",
   'finally',
   'got',
   'it',
   'rightI',
   'wonder',
   'if',
   'he',
   'knows',
   "he's",
   'all',
   'I',
   'think',
   'about',
   'at',
   "nightHe's",
   'the',
   'reason',
   'for',
   'the',
   'teardrops',
   'on',
   'my',
   'guitarThe',
   'only',
   'thing',
   'that',
   

In [13]:
with open("album_lyrics_1.json", 'w') as f:
        json.dump(album_lyrics_obj, f, indent=4)

### Construct pandas dataframe

In [14]:
lyrics_df = pd.DataFrame(data=song_lyrics_obj)
lyrics_df

song_title                     album  \
0                                   cardigan                   folklore   
1                                      exile                   folklore   
2                                      lover                    unknown   
3                                      the 1                   folklore   
4                   look what you made me do                 reputation   
..                                        ...                       ...   
295                      check out this view           unreleased songs   
296                                  my cure           unreleased songs   
297                                 sunshine           unreleased songs   
298  i forgot that you existed (piano/vocal)                    unknown   
299      you're not sorry (taylor's version)   fearless taylors version   

                                                lyrics  
0    [Vintage, tee,, brand, new, phoneHigh, heels, ...  
1    [I, can, see, you, standing,, honeyWith, his, ...  
2    [We, could, leave, the, Christmas, lights, up,...  
3    [I'm, doing, good,, I'm, on, some, new, shitBe...  
4    [I, don't, like, your, little, gamesDon't, lik...  
..                                                 ...  
295  [I, dont, need, a, lotBut, there's, one, thing...  
296  [I, know, we've, got, a, lot, to, sayBetween, ...  
297  [I, walk, in, the, room, there's, a, beautiful...  
298  [So, the, clip, that, you're, about, to, hearI...  
299  [All, this, time, I, was, wasting, hoping, you...  

[300 rows x 3 columns]

### Save dataframe to csv file for storage in PostgreSQL database.

In [15]:
lyrics_df.to_csv('lyrics_df.csv',index=False)